In [1]:
import pandas as pd 
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
import string
from collections import Counter
import math

In [2]:
# Reading the training and testing data into dataframes from the csv files.
train_data = pd.read_csv("spotify_train.csv")
test_data = pd.read_csv("spotify_test.csv")

In [3]:
#Printing the head to make sure the data is imported correctly.
train_data.head()

popularity  duration_ms  explicit  danceability  energy  key  loudness  \
0           0       211682      True         0.732   0.635    1    -7.891   
1           1       223613     False         0.409   0.570    6   -10.540   
2          56       243626     False         0.536   0.764    1    -5.174   
3           8       182413      True         0.843   0.789    7    -2.801   
4          74       200120     False         0.535   0.765    1    -7.862   

   mode  speechiness  acousticness  instrumentalness  liveness  valence  \
0     1       0.4100        0.4930          0.000007    0.3880    0.581   
1     0       0.0711        0.6870          0.000000    0.1730    0.336   
2     0       0.0393        0.0302          0.000011    0.1040    0.294   
3     1       0.2470        0.0028          0.000024    0.0322    0.571   
4     0       0.0444        0.0540          0.000000    0.0921    0.373   

     tempo  time_signature track_genre  
0  147.025               4     hip-hop  
1  128.657               4         pop  
2  147.585               4        rock  
3  125.071               4     hip-hop  
4  191.827               4         pop

In [4]:
# number of columns in train data
len(train_data.columns)

16

In [5]:
train_data['duration_ms']

0       211682
1       223613
2       243626
3       182413
4       200120
         ...  
1995    206696
1996    550706
1997    331266
1998    199263
1999    232258
Name: duration_ms, Length: 2000, dtype: int64

In [6]:
#Dropping the duration column because to optimize efficiency
train_data = train_data.drop('duration_ms', axis=1)

In [7]:
# verfiy that duration column was dropped
len(train_data.columns)

15

In [8]:
# remove duplicates
train_data.drop_duplicates(inplace=False)

popularity  explicit  danceability  energy  key  loudness  mode  \
0              0      True         0.732   0.635    1    -7.891     1   
1              1     False         0.409   0.570    6   -10.540     0   
2             56     False         0.536   0.764    1    -5.174     0   
3              8      True         0.843   0.789    7    -2.801     1   
4             74     False         0.535   0.765    1    -7.862     0   
...          ...       ...           ...     ...  ...       ...   ...   
1995           0     False         0.741   0.695    1    -5.341     1   
1996           2     False         0.765   0.833   10    -5.162     0   
1997          81     False         0.577   0.828    6    -8.691     0   
1998          48     False         0.754   0.802    9    -6.424     1   
1999          70     False         0.824   0.543    4    -8.667     0   

      speechiness  acousticness  instrumentalness  liveness  valence    tempo  \
0          0.4100       0.49300          0.000007    0.3880    0.581  147.025   
1          0.0711       0.68700          0.000000    0.1730    0.336  128.657   
2          0.0393       0.03020          0.000011    0.1040    0.294  147.585   
3          0.2470       0.00280          0.000024    0.0322    0.571  125.071   
4          0.0444       0.05400          0.000000    0.0921    0.373  191.827   
...           ...           ...               ...       ...      ...      ...   
1995       0.0454       0.02100          0.000000    0.0922    0.861  134.032   
1996       0.0873       0.03760          0.268000    0.0824    0.837  126.422   
1997       0.0298       0.00213          0.011400    0.0581    0.604  123.257   
1998       0.0551       0.03490          0.000000    0.3350    0.583  122.026   
1999       0.2090       0.10100          0.000000    0.1780    0.548  124.018   

      time_signature track_genre  
0                  4     hip-hop  
1                  4         pop  
2                  4        rock  
3                  4     hip-hop  
4                  4         pop  
...              ...         ...  
1995               4         pop  
1996               4        rock  
1997               4        rock  
1998               4        rock  
1999               4     hip-hop  

[1691 rows x 15 columns]

In [9]:
#Printing the head to make sure the data is imported correctly.
test_data.head()

popularity  duration_ms  explicit  danceability  energy  key  loudness  \
0           0       169756     False         0.601   0.713    4    -3.758   
1          66        87133     False         0.638   0.324    0    -7.787   
2           1       242640     False         0.660   0.752    6    -5.839   
3          71       242628     False         0.697   0.663    6    -7.246   
4           0       214733     False         0.552   0.823    2    -5.988   

   mode  speechiness  acousticness  instrumentalness  liveness  valence  \
0     0       0.0449        0.0282          0.000000     0.158    0.464   
1     0       0.0321        0.9230          0.000034     0.151    0.446   
2     1       0.0487        0.2510          0.003980     0.322    0.934   
3     1       0.0486        0.0701          0.000010     0.112    0.407   
4     1       0.0332        0.4450          0.000129     0.366    0.775   

     tempo  time_signature track_genre  
0  122.872               4         pop  
1  129.932               4         pop  
2  159.684               4        rock  
3   96.968               4     hip-hop  
4  114.514               4        rock

In [10]:
#Encoding the explicit column to be represented as 1's and 0's.
train_data['explicit'] = train_data['explicit'].astype(int)
test_data['explicit'] = test_data['explicit'].astype(int)

In [24]:
# adds up the values
def total(cnt):
    return sum(cnt.values())

In [25]:
# function to find the gini
def gini(counter):
    tot = total(counter)
    return 1 - sum([(v/tot)**2 for v in counter.values()])

In [26]:
from math import log2

# function to find the entropy
def entropy(counter):
    tot = total(counter)
    return sum([(-v/tot) * log2(v/tot) for v in counter.values()])

In [27]:
# function to run the correct impurity score based on criterion
def impurity(data, criterion):
    counts = Counter(data['track_genre'])
    if criterion == 'gini':
        return gini(counts)
    else:
        return entropy(counts)

In [28]:
# function to calculate weighted average 
def wavg(cnt1, cnt2, measure):
    tot1 = total(cnt1)
    tot2 = total(cnt2)
    tot = tot1 + tot2
    return round(((measure(cnt1) * tot1 + measure(cnt2) * tot2) / tot), 4)

In [29]:
# function to evaluate the split using class_col and split_col
def evaluate_split(train_data, class_col, split_col, feature_val, measure):
    # create two dataframes based on left and right split using the feature value
    df1, df2 = train_data[train_data[split_col] >= feature_val], train_data[train_data[split_col] < feature_val]
    # return the count of the dataframe for the class_col
    cnt1, cnt2 = Counter(df1[class_col]), Counter(df2[class_col])
    # calculate weighted average
    return wavg(cnt1, cnt2, measure)

In [30]:
# What is the depth of the tree?
# The depth is the Maximum number of "steps" to any leaf
def depth(T):
    """ Return the maximum depth of the tree """
    if T is None:
        return -1
    else:
        return 1 + max(depth(left(T)), depth(right(T)))

In [31]:
# function to caluclate best split based on a given impurity method
def best_split(df, class_col, method):
    best_col = 0
    best_v = 0.0
    best_meas = float("inf")
    
    # for each column in the dataframe...
    for split_col in df.columns:
        # if the column is not the class_col
        if split_col != class_col:
            # calculate the best split for that column and the measure it returns
            v, meas = best_split_for_column(df, class_col, split_col, method)
            if meas < best_meas:
                # if the new measure is less than the current best, update the values
                best_v = v
                best_meas = meas
                best_col = split_col
    # return the best column, best threshold, and best measure
    return best_col, best_v, best_meas

In [32]:
def best_split_for_column(train_data, class_col, split_col, method):
    best_v = ''
    best_meas = float("inf")
    
    # for each value of the split_col
    for v in set(train_data[split_col]):
        # evaluate the split to determine which split value is best for that column
        meas = evaluate_split(train_data, class_col, split_col, v, method)
        # if the new measure is better than the previous one, replace the values as needed
        if  meas < best_meas:
            best_v = v
            best_meas = meas
    
    # return the best threshold and best measure
    return best_v, best_meas

In [33]:
# function to calculate the dtree given a train set and criterion
def dtree(train, criterion, max_depth=None, min_instances=2, target_impurity=0.0, depth=0):        
    # Base case 1: length of the track_genre column in dataframe is one
    if len(train['track_genre'].unique()) == 1:
        majority_class = train['track_genre'].iloc[0]
        # return the leaf with an impurity score of 0
        return ('leaf', None, majority_class, 0, depth, None, None)

    # Base case 2: maximum depth reached
    if max_depth is not None and max_depth == 0:
        majority_class = train['track_genre'].mode()[0]
        impurity_score = impurity(train, criterion)
        # return the leaf with the calculate majority class and impurity score
        return ('leaf', None, majority_class, impurity_score, depth, None, None)

    # Base case 3: not enough instances to split
    if len(train) < min_instances:
        majority_class = train['track_genre'].mode()[0]
        impurity_score = impurity(train, criterion)
        # return the leaf with the calculate majority class and impurity score
        return ('leaf', None, majority_class, impurity_score, depth, None, None)
    
    # find the best column, best threshold and best measure for the train set and the given criterion
    best_col, best_v, best_meas = best_split(train, 'track_genre', criterion)
    # split to a left and right branch based on the threshold
    left_df, right_df = train[train[best_col] < best_v], train[train[best_col] >= best_v]
    # add to the depth
    newDepth = depth + 1
    
    # Base Case 4: if length of the new dataframes or the original dataframe is 0, return a leaf
    if (len(train) == 0) or (len(left_df) == 0) or (len(right_df) == 0):
        combined_df = pd.concat([train, left_df, right_df])
        majority_class = combined_df['track_genre'].mode()[0]
        return ('leaf', None, majority_class, 0, newDepth, None, None)
    
    # Base Case 5: if the best measure is less than the target impurity value, return a leaf
    if (best_meas < target_impurity):
        majority_class = train['track_genre'].iloc[0]
        return ('leaf', None, majority_class, best_meas, newDepth, None, None)
    
    #If none of the base cases are hit, record the data for the tuple and recur right and left.
    return (best_col, best_v, train['track_genre'].mode()[0], best_meas, depth, \
            dtree(left_df, criterion, None if max_depth is None else max_depth-1, \
                  min_instances, target_impurity, newDepth), dtree(right_df, criterion, \
                                      None if max_depth is None else max_depth-1, \
                                      min_instances, target_impurity, newDepth)) 

In [70]:
#Default model with max_depth of None, min_instances = 0, target_impurity = 0.0.
first_model = dtree(train_data, gini)

In [71]:
#Ensuring the model printed properly and stores the data in accordance.
first_model

('danceability',
 0.706,
 'rock',
 0.589,
 0,
 ('popularity',
  3,
  'rock',
  0.5454,
  1,
  ('mode',
   1,
   'rock',
   0.4002,
   2,
   ('instrumentalness',
    1.81e-05,
    'rock',
    0.4906,
    3,
    ('acousticness',
     0.345,
     'pop',
     0.5076,
     4,
     ('danceability',
      0.559,
      'rock',
      0.5219,
      5,
      ('speechiness',
       0.323,
       'rock',
       0.0,
       6,
       ('leaf', None, 'rock', 0, 7, None, None),
       ('leaf', None, 'hip-hop', 0, 7, None, None)),
      ('loudness',
       -3.949,
       'pop',
       0.5084,
       6,
       ('acousticness',
        0.072,
        'hip-hop',
        0.4078,
        7,
        ('key',
         3,
         'hip-hop',
         0.368,
         8,
         ('explicit',
          1,
          'pop',
          0.0,
          9,
          ('leaf', None, 'pop', 0, 10, None, None),
          ('leaf', None, 'hip-hop', 0, 10, None, None)),
         ('instrumentalness',
          3.15e-06,
        

In [36]:
#Given an already constructed model, function takes in a row of data and uses the model
# to predict the class of the model.
def predictRow(model, row):
    if model[0] == 'leaf':
        return model[2]
    else:  
        if (row[model[0]] < model[1]):
            return predictRow(model[5], row)
        else:
            return predictRow(model[6], row)

In [37]:
#Predicts an entire dataframe using an already constructed model.
def predict(model, data):
    listPredictions = []
    for i in range(data.shape[0]):
        listPredictions.append(predictRow(model, data.iloc[i]))
    return listPredictions

In [38]:
# Calculates the accuracy of a series of predictions and actual class values.
def accuracyfunc(y, ypred):
    totalsum = len(y)
    numCorrect = 0
    for i in range(len(y)):
        if (y[i] == ypred[i]):
            numCorrect += 1
    return numCorrect/totalsum

In [39]:
#Utilized to more accurately determine if a model is ouputting accurate results without using the test data.
def ten_fold_validation(training_data, criterion, max_depth=None, min_instances=2, target_impurity=0.0, depth=0):
    accuracyList = []
    for f in range(10):
        train_fold = training_data[training_data.index % 10 != f].reset_index(drop=True)
        valid_fold = training_data[training_data.index % 10 == f].reset_index(drop=True)
        model = dtree(train_fold, criterion, max_depth=None, min_instances=2, target_impurity=0.0, depth=0)
        ypred = predict(model, valid_fold)
        y = valid_fold['track_genre']
        accuracy = accuracyfunc(y, ypred)
        accuracyList.append(accuracy)
    return (sum(accuracyList) / 10)

In [49]:
# Determining the accuracy on the validation data.
print("The accuracy on the validation data is:", ten_fold_validation(train_data, gini))

The accuracy on the validation data is: 0.724


In [42]:
# Streamlined function to optimize runtime for the hyperparameter_tuning.
# Only uses one fold as opposed to ten. 
def test_hypermodel(training_data, criterion, max_depth, min_instances, target_impurity):
    train_len = int((len(training_data) * 0.80))
    valid_len = int((len(training_data) * 0.20))
    train_fold = training_data.head(train_len).reset_index(drop=True)
    valid_fold = training_data.tail(valid_len).reset_index(drop=True)
    model = dtree(train_fold, criterion, max_depth, min_instances, target_impurity)
    print(model)
    ypred = predict(model, valid_fold)
    y = valid_fold['track_genre']
    accuracy = accuracyfunc(y, ypred)
    return accuracy

In [43]:
#Function needed to determine the best parameters of the model for the decision tree.
def hyperparameter_tuning(train):
    best_accuracy = 0
    criterions = [gini, entropy]
    max_depths = np.arange(4, 14, 1)
    min_instances = np.arange(2, 14, 1)
    target_impurities = np.arange(0.0, 0.35, 0.05)
   
    for c in criterions:
        for md in max_depths:
            for mi in min_instances:
                for ti in target_impurities:
#                     model = dtree(train, c, md, mi, ti)
                    accuracy = test_hypermodel(train, c, md, mi, ti)
                    print(c, md, mi, ti, accuracy)
                    if accuracy > best_accuracy:
                        best_accuracy = accuracy
                        best_params = c, md, mi, ti
    return best_params

In [44]:
# Shuffling the data and taking the first 400 values to use to tune the model.
shuffled_data = train_data.sample(frac=1).reset_index(drop=True).head(400)

In [45]:
# getting the best parameters for our model.
best_params = hyperparameter_tuning(shuffled_data)

('danceability', 0.695, 'rock', 0.5723, 0, ('popularity', 56, 'rock', 0.4888, 1, ('acousticness', 0.811, 'rock', 0.2885, 2, ('speechiness', 0.0531, 'rock', 0.2688, 3, ('leaf', None, 'rock', 0.46328187072785876, 4, None, None), ('leaf', None, 'rock', 1.3787834934861753, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 0.4642, 2, ('loudness', -2.625, 'hip-hop', 0.0588, 3, ('leaf', None, 'hip-hop', 0, 4, None, None), ('leaf', None, 'hip-hop', 1.0, 4, None, None)), ('popularity', 75, 'pop', 0.3854, 3, ('leaf', None, 'pop', 0.8820390213448125, 4, None, None), ('leaf', None, 'rock', 1.14630864593417, 4, None, None)))), ('popularity', 65, 'hip-hop', 0.3902, 1, ('speechiness', 0.0318, 'hip-hop', 0.2601, 2, ('danceability', 0.765, 'rock', 0.0, 3, ('leaf', None, 'pop', 0, 4, None, None), ('leaf', None, 'rock', 0, 4, None, None)), ('tempo', 167.969, 'hip-hop', 0.2086, 3, ('leaf', None, 'hip-hop', 0.540449412645123, 4, None, None), ('leaf', None, 'pop', 0.970950

('danceability', 0.695, 'rock', 0.5723, 0, ('popularity', 56, 'rock', 0.4888, 1, ('acousticness', 0.811, 'rock', 0.2885, 2, ('speechiness', 0.0531, 'rock', 0.2688, 3, ('leaf', None, 'rock', 0.46328187072785876, 4, None, None), ('leaf', None, 'rock', 1.3787834934861753, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 0.4642, 2, ('loudness', -2.625, 'hip-hop', 0.0588, 3, ('leaf', None, 'hip-hop', 0, 4, None, None), ('leaf', None, 'hip-hop', 1.0, 4, None, None)), ('popularity', 75, 'pop', 0.3854, 3, ('leaf', None, 'pop', 0.8820390213448125, 4, None, None), ('leaf', None, 'rock', 1.14630864593417, 4, None, None)))), ('popularity', 65, 'hip-hop', 0.3902, 1, ('speechiness', 0.0318, 'hip-hop', 0.2601, 2, ('leaf', None, 'rock', 0.0, 4, None, None), ('tempo', 167.969, 'hip-hop', 0.2086, 3, ('leaf', None, 'hip-hop', 0.540449412645123, 4, None, None), ('leaf', None, 'pop', 0.9709505944546686, 4, None, None))), ('danceability', 0.841, 'pop', 0.3995, 2, ('tempo'

('danceability', 0.695, 'rock', 0.5723, 0, ('popularity', 56, 'rock', 0.4888, 1, ('acousticness', 0.811, 'rock', 0.2885, 2, ('speechiness', 0.0531, 'rock', 0.2688, 3, ('leaf', None, 'rock', 0.46328187072785876, 4, None, None), ('leaf', None, 'rock', 1.3787834934861753, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 0.4642, 2, ('leaf', None, 'hip-hop', 0.0588, 4, None, None), ('popularity', 75, 'pop', 0.3854, 3, ('leaf', None, 'pop', 0.8820390213448125, 4, None, None), ('leaf', None, 'rock', 1.14630864593417, 4, None, None)))), ('popularity', 65, 'hip-hop', 0.3902, 1, ('speechiness', 0.0318, 'hip-hop', 0.2601, 2, ('leaf', None, 'rock', 0.9182958340544896, 3, None, None), ('tempo', 167.969, 'hip-hop', 0.2086, 3, ('leaf', None, 'hip-hop', 0.540449412645123, 4, None, None), ('leaf', None, 'pop', 0.9709505944546686, 4, None, None))), ('danceability', 0.841, 'pop', 0.3995, 2, ('tempo', 93.012, 'pop', 0.3343, 3, ('leaf', None, 'hip-hop', 1.286692668354754

('danceability', 0.695, 'rock', 0.5723, 0, ('popularity', 56, 'rock', 0.4888, 1, ('acousticness', 0.811, 'rock', 0.2885, 2, ('speechiness', 0.0531, 'rock', 0.2688, 3, ('leaf', None, 'rock', 0.46328187072785876, 4, None, None), ('leaf', None, 'rock', 1.3787834934861753, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 0.4642, 2, ('leaf', None, 'hip-hop', 0.0588, 4, None, None), ('popularity', 75, 'pop', 0.3854, 3, ('leaf', None, 'pop', 0.8820390213448125, 4, None, None), ('leaf', None, 'rock', 1.14630864593417, 4, None, None)))), ('popularity', 65, 'hip-hop', 0.3902, 1, ('speechiness', 0.0318, 'hip-hop', 0.2601, 2, ('leaf', None, 'rock', 0.9182958340544896, 3, None, None), ('tempo', 167.969, 'hip-hop', 0.2086, 3, ('leaf', None, 'hip-hop', 0.540449412645123, 4, None, None), ('leaf', None, 'pop', 0.9709505944546686, 4, None, None))), ('danceability', 0.841, 'pop', 0.3995, 2, ('tempo', 93.012, 'pop', 0.3343, 3, ('leaf', None, 'hip-hop', 1.286692668354754

('danceability', 0.695, 'rock', 0.5723, 0, ('popularity', 56, 'rock', 0.4888, 1, ('acousticness', 0.811, 'rock', 0.2885, 2, ('speechiness', 0.0531, 'rock', 0.2688, 3, ('leaf', None, 'rock', 0.46328187072785876, 4, None, None), ('leaf', None, 'rock', 1.3787834934861753, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 0.4642, 2, ('leaf', None, 'hip-hop', 0.0588, 4, None, None), ('popularity', 75, 'pop', 0.3854, 3, ('leaf', None, 'pop', 0.8820390213448125, 4, None, None), ('leaf', None, 'rock', 1.14630864593417, 4, None, None)))), ('popularity', 65, 'hip-hop', 0.3902, 1, ('speechiness', 0.0318, 'hip-hop', 0.2601, 2, ('leaf', None, 'rock', 0.9182958340544896, 3, None, None), ('tempo', 167.969, 'hip-hop', 0.2086, 3, ('leaf', None, 'hip-hop', 0.540449412645123, 4, None, None), ('leaf', None, 'pop', 0.9709505944546686, 4, None, None))), ('danceability', 0.841, 'pop', 0.3995, 2, ('tempo', 93.012, 'pop', 0.3343, 3, ('leaf', None, 'hip-hop', 1.286692668354754

...

('danceability', 0.695, 'rock', 1.366, 0, ('popularity', 56, 'rock', 1.2037, 1, ('acousticness', 0.811, 'rock', 0.7816, 2, ('instrumentalness', 0.000136, 'rock', 0.6997, 3, ('mode', 1, 'rock', 0.8822, 4, ('danceability', 0.626, 'pop', 0.7663, 5, ('acousticness', 0.46, 'pop', 0.4636, 6, ('leaf', None, 'rock', 0.8112781244591328, 7, None, None), ('leaf', None, 'pop', 0, 7, None, None)), ('leaf', None, 'hip-hop', 0, 6, None, None)), ('popularity', 1, 'rock', 0.4507, 5, ('leaf', None, 'rock', 0.0, 7, None, None), ('tempo', 173.372, 'rock', 0.637, 6, ('loudness', -6.312, 'rock', 0.4598, 7, ('leaf', None, 'rock', 0, 8, None, None), ('leaf', None, 'rock', 0.9852281360342516, 8, None, None)), ('leaf', None, 'pop', 0, 7, None, None)))), ('leaf', None, 'rock', 0, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 1.113, 2, ('leaf', None, 'hip-hop', 0.1176, 4, None, None), ('popularity', 73, 'pop', 0.9882, 3, ('acousticness', 0.119, 'pop', 0.5646, 4, ('leaf', Non

('danceability', 0.695, 'rock', 1.366, 0, ('popularity', 56, 'rock', 1.2037, 1, ('acousticness', 0.811, 'rock', 0.7816, 2, ('instrumentalness', 0.000136, 'rock', 0.6997, 3, ('mode', 1, 'rock', 0.8822, 4, ('danceability', 0.626, 'pop', 0.7663, 5, ('acousticness', 0.46, 'pop', 0.4636, 6, ('leaf', None, 'rock', 0.8112781244591328, 7, None, None), ('leaf', None, 'pop', 0, 7, None, None)), ('leaf', None, 'hip-hop', 0, 6, None, None)), ('popularity', 1, 'rock', 0.4507, 5, ('leaf', None, 'rock', 0.0, 7, None, None), ('tempo', 173.372, 'rock', 0.637, 6, ('loudness', -6.312, 'rock', 0.4598, 7, ('leaf', None, 'rock', 0, 8, None, None), ('leaf', None, 'rock', 0.9852281360342516, 8, None, None)), ('leaf', None, 'pop', 0, 7, None, None)))), ('leaf', None, 'rock', 0, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 1.113, 2, ('loudness', -2.625, 'hip-hop', 0.1176, 3, ('leaf', None, 'hip-hop', 0, 4, None, None), ('leaf', None, 'hip-hop', 1.0, 4, None, None)), ('pop

('danceability', 0.695, 'rock', 1.366, 0, ('popularity', 56, 'rock', 1.2037, 1, ('acousticness', 0.811, 'rock', 0.7816, 2, ('instrumentalness', 0.000136, 'rock', 0.6997, 3, ('mode', 1, 'rock', 0.8822, 4, ('danceability', 0.626, 'pop', 0.7663, 5, ('acousticness', 0.46, 'pop', 0.4636, 6, ('leaf', None, 'rock', 0.8112781244591328, 7, None, None), ('leaf', None, 'pop', 0, 7, None, None)), ('leaf', None, 'hip-hop', 0, 6, None, None)), ('popularity', 1, 'rock', 0.4507, 5, ('leaf', None, 'rock', 0.0, 7, None, None), ('tempo', 173.372, 'rock', 0.637, 6, ('loudness', -6.312, 'rock', 0.4598, 7, ('leaf', None, 'rock', 0, 8, None, None), ('leaf', None, 'rock', 0.9852281360342516, 8, None, None)), ('leaf', None, 'pop', 0, 7, None, None)))), ('leaf', None, 'rock', 0, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 1.113, 2, ('leaf', None, 'hip-hop', 0.1176, 4, None, None), ('popularity', 73, 'pop', 0.9882, 3, ('acousticness', 0.119, 'pop', 0.5646, 4, ('leaf', Non

('danceability', 0.695, 'rock', 1.366, 0, ('popularity', 56, 'rock', 1.2037, 1, ('acousticness', 0.811, 'rock', 0.7816, 2, ('instrumentalness', 0.000136, 'rock', 0.6997, 3, ('mode', 1, 'rock', 0.8822, 4, ('danceability', 0.626, 'pop', 0.7663, 5, ('acousticness', 0.46, 'pop', 0.4636, 6, ('leaf', None, 'rock', 0.8112781244591328, 7, None, None), ('leaf', None, 'pop', 0, 7, None, None)), ('leaf', None, 'hip-hop', 0, 6, None, None)), ('popularity', 1, 'rock', 0.4507, 5, ('leaf', None, 'rock', 0.0, 7, None, None), ('tempo', 173.372, 'rock', 0.637, 6, ('loudness', -6.312, 'rock', 0.4598, 7, ('leaf', None, 'rock', 0, 8, None, None), ('leaf', None, 'rock', 0.9852281360342516, 8, None, None)), ('leaf', None, 'pop', 0, 7, None, None)))), ('leaf', None, 'rock', 0, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 1.113, 2, ('loudness', -2.625, 'hip-hop', 0.1176, 3, ('leaf', None, 'hip-hop', 0, 4, None, None), ('leaf', None, 'hip-hop', 1.0, 4, None, None)), ('pop

('danceability', 0.695, 'rock', 1.366, 0, ('popularity', 56, 'rock', 1.2037, 1, ('acousticness', 0.811, 'rock', 0.7816, 2, ('instrumentalness', 0.000136, 'rock', 0.6997, 3, ('mode', 1, 'rock', 0.8822, 4, ('danceability', 0.626, 'pop', 0.7663, 5, ('acousticness', 0.46, 'pop', 0.4636, 6, ('leaf', None, 'rock', 0.8112781244591328, 7, None, None), ('leaf', None, 'pop', 0, 7, None, None)), ('leaf', None, 'hip-hop', 0, 6, None, None)), ('popularity', 1, 'rock', 0.4507, 5, ('leaf', None, 'rock', 0.0, 7, None, None), ('tempo', 173.372, 'rock', 0.637, 6, ('loudness', -6.312, 'rock', 0.4598, 7, ('leaf', None, 'rock', 0, 8, None, None), ('leaf', None, 'rock', 0.9852281360342516, 8, None, None)), ('leaf', None, 'pop', 0, 7, None, None)))), ('leaf', None, 'rock', 0, 4, None, None)), ('leaf', None, 'pop', 0, 3, None, None)), ('popularity', 65, 'pop', 1.113, 2, ('leaf', None, 'hip-hop', 0.1176, 4, None, None), ('popularity', 73, 'pop', 0.9882, 3, ('acousticness', 0.119, 'pop', 0.5646, 4, ('leaf', Non

In [47]:
#Printing the best parameters for our model.
best_params

(<function __main__.entropy(counter)>, 6, 2, 0.0)

In [48]:
# Running our tuned optimized model on the test set.
optimized_model = dtree(train_data, entropy, 6, 2)
ypred = predict(optimized_model, test_data)
y = test_data['track_genre']
accuracy = accuracyfunc(y, ypred)
print("The accuracy of our tuned model on the test set is:", accuracy)

The accuracy of our tuned model on the test set is: 0.741


In [65]:
# Printing our optimized model
optimized_model

('danceability',
 0.706,
 'rock',
 1.4045,
 0,
 ('popularity',
  55,
  'rock',
  1.3205,
  1,
  ('mode',
   1,
   'rock',
   1.0726,
   2,
   ('instrumentalness',
    1.08e-05,
    'rock',
    1.2399,
    3,
    ('acousticness',
     0.345,
     'pop',
     1.2807,
     4,
     ('danceability',
      0.559,
      'pop',
      1.3039,
      5,
      ('leaf', None, 'rock', 0.6583514224564075, 6, None, None),
      ('leaf', None, 'pop', 1.492844037499991, 6, None, None)),
     ('danceability',
      0.7,
      'pop',
      0.1808,
      5,
      ('leaf', None, 'pop', 0.19143325481419343, 6, None, None),
      ('leaf', None, 'rock', 0, 6, None, None))),
    ('danceability',
     0.588,
     'rock',
     0.6786,
     4,
     ('acousticness',
      0.138,
      'rock',
      0.2699,
      5,
      ('leaf', None, 'rock', 0, 6, None, None),
      ('leaf', None, 'rock', 1.295461844238322, 6, None, None)),
     ('valence',
      0.454,
      'rock',
      0.6828,
      5,
      ('leaf', None, 'p

In [66]:
import random
from collections import Counter
# Bagging models algorithm which is utilized to combine multiple models together and take the overall consensus
# to form a prediction.
# Trained on the training data and tested on the testing data.
# Was mentioned in class for extra credit opportunity.
def bagging_models(ensemble_size=125):
    predictions = []
    final_predictions = []
    for i in range(ensemble_size):
        # Creates the models with random parameters.
        newModel = dtree(train_data, [gini, entropy][random.randint(0, 1)], max_depth=random.randint(4, 14), \
                         min_instances=random.randint(2, 14), target_impurity=random.uniform(0.0, 0.35))
        y_pred = predict(newModel, test_data)
        predictions.append(y_pred)
    arr = np.array(predictions)
    for j in range(len(test_data)):
        c = Counter(arr[:, j])
        final_predictions.append(c.most_common(1)[0][0])
    accuracy = accuracyfunc(test_data['track_genre'], final_predictions)
    return accuracy

In [69]:
# Printing the accuracy when utilizing the bagging models algorithm.
acc = bagging_models()
print("The accuracy when bagging models with random attributes to draw consensus is", acc)

The accuracy when bagging models to draw consensus is 0.73


In [91]:
# Bagging models algorithm which is utilized to combine multiple models together and take the overall consensus
# to form a prediction.
# Trained on the training data and tested on the testing data.
# Was mentioned in class for extra credit opportunity.
# This algorithm trains models on different subsets of the data with the most optimal model.
def bagging_models_trained_diff(ensemble_size=10):
    predictions = []
    final_predictions = []
    subset_size_train = len(train_data) // ensemble_size
    subsets_train = [train_data[i:i+subset_size_train] for i in range(0, len(train_data), subset_size_train)]
    for i in range(ensemble_size):
        # Creates the models with optimal attributes. 
        newModel = dtree(subsets_train[i], entropy, 6, 2)
        y_pred = predict(newModel, test_data)
        predictions.append(y_pred)
    arr = np.array(predictions)
    for j in range(len(test_data)):
        c = Counter(arr[:, j])
        final_predictions.append(c.most_common(1)[0][0])
    accuracy = accuracyfunc(test_data['track_genre'], final_predictions)
    return accuracy

In [92]:
accuracy = bagging_models_trained_diff()
print("The accuracy when bagging models with optimal attributes but training on different subsets of the data is", accuracy)

The accuracy when bagging models with optimal attributes but training on different subsets of the data is 0.736
